# 🚀 Baseline XGBoost for Resource Estimation of CNNs (Keras Applications)
This notebook demonstrates how to use XGBoost for predicting resource usage (like fit time) of CNN models based on dataset features.

## 1️⃣ Setup and Installation
Ensure required libraries are installed.

In [1]:
!pip uninstall -y scikit-learn
!pip install scikit-learn==1.5.2

Found existing installation: scikit-learn 1.6.1
Uninstalling scikit-learn-1.6.1:
  Successfully uninstalled scikit-learn-1.6.1
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.3/13.3 MB 34.5 MB/s eta 0:00:00


## 2️⃣ Import Libraries
Import all necessary Python libraries for data handling, modeling, and visualization.

In [2]:
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error
from xgboost import XGBRegressor
import joblib

## 3️⃣ Data Loading & Preprocessing
Load the dataset and perform basic preprocessing to prepare for modeling.

In [3]:
def calculate_mspe_rmspe(y_true, y_pred):
    mape = np.mean(np.abs((y_true - y_pred) / (y_true)), axis=0) * 100
    mspe = np.mean(((y_true - y_pred) / y_true) ** 2, axis=0) * 100  # MSPE for each column
    rmspe = np.sqrt(mspe)  # RMSPE for each column
    return mape, mspe, rmspe



In [7]:
# Load data
# Assuming the data is in a CSV file with the target column 'fit_time_in_TF'
data_path = 'dataset-new.csv'  # Replace with the actual path to your dataset
df = pd.read_csv(data_path)
# Another way is to directly load the data from the hugging face where the dataset is hosted
# url = 'https://huggingface.co/datasets/ICICLE-AI/ResourceEstimation_HLOGenCNN/resolve/main/dataset-new.csv'
# df = pd.read_csv(url)
df.columns

Index(['name', 'samples', 'input_dim_w', 'input_dim_h', 'input_dim_c',
       'output_dim', 'optimizer', 'epochs', 'batch', 'learn_rate',
       'tf_version', 'cuda_version', 'batch_time', 'epoch_time', 'fit_time',
       'npz_path', 'gpu_make', 'gpu_name', 'gpu_arch', 'gpu_cc',
       'gpu_core_count', 'gpu_sm_count', 'gpu_memory_size', 'gpu_memory_type',
       'gpu_memory_bw', 'gpu_tensor_core_count', 'max_memory_util',
       'avg_memory_util', 'max_gpu_util', 'avg_gpu_util', 'max_gpu_temp',
       'avg_gpu_temp'],
      dtype='object')

## 4️⃣ Feature Engineering
Extract relevant features and clean the dataset.

In [8]:
# Extract substring before the first underscore
df['unit_name'] = df['name'].str.split('_').str[0]

# Display the updated DataFrame
print(df[['name', 'unit_name']].head())

                                                name  unit_name
0  MobileNet_architecture_optadam_s1_ipd224x224x3...  MobileNet
1  MobileNet_architecture_optadam_s1_ipd224x224x3...  MobileNet
2  MobileNet_architecture_optadam_s1_ipd224x224x3...  MobileNet
3  MobileNet_architecture_optadam_s1_ipd224x224x3...  MobileNet
4  MobileNet_architecture_optadam_s1_ipd224x224x3...  MobileNet


In [9]:
df = df.dropna()  # Dropping rows with missing values (you can customize this)

from sklearn.preprocessing import LabelEncoder
label_encoder = LabelEncoder()
# Transform the categorical column
df['unit_name_encoded'] = label_encoder.fit_transform(df['unit_name'])
# Optional: Mapping of encoded labels to original categories
mapping = dict(zip(label_encoder.classes_, range(len(label_encoder.classes_))))
print("\nLabel Mapping:", mapping)

df = df.drop(columns=['name', 'npz_path', 'unit_name'])
# Convert categorical features to numeric (if any)
df = pd.get_dummies(df, drop_first=True)



Label Mapping: {'DenseNet121': 0, 'DenseNet169': 1, 'DenseNet201': 2, 'EfficientNetB0': 3, 'EfficientNetB1': 4, 'EfficientNetB7': 5, 'InceptionV3': 6, 'MobileNet': 7, 'MobileNetV2': 8, 'NASNetLarge': 9, 'NASNetMobile': 10, 'ResNet101': 11, 'ResNet152': 12, 'ResNet50': 13, 'VGG16': 14, 'VGG19': 15, 'Xception': 16}


In [10]:
df.head()

samples  input_dim_w  input_dim_h  input_dim_c  output_dim  epochs  batch  \
0        1          224          224            3          10       1      1   
1        1          224          224            3          10       1      1   
2        1          224          224            3          10       1      1   
3        1          224          224            3          10       2      1   
4        1          224          224            3          10       2      1   

   learn_rate  cuda_version  batch_time  ...  max_gpu_util  avg_gpu_util  \
0      0.0100          12.2       22.07  ...          13.0          0.51   
1      0.0010          12.2       18.44  ...         100.0          2.92   
2      0.0001          12.2       18.78  ...          26.0          0.86   
3      0.0100          12.2        9.38  ...          28.0          1.78   
4      0.0010          12.2        9.30  ...         100.0          3.41   

   max_gpu_temp  avg_gpu_temp  unit_name_encoded  optimizer_sgd  \
0          25.0         25.00                  7          False   
1          26.0         25.84                  7          False   
2          26.0         26.00                  7          False   
3          27.0         26.04                  7          False   
4          27.0         26.55                  7          False   

   gpu_name_Tesla P100-PCIE-16GB  gpu_name_Tesla V100S-PCIE-32GB  \
0                           True                           False   
1                           True                           False   
2                           True                           False   
3                           True                           False   
4                           True                           False   

   gpu_arch_Tesla  gpu_memory_type_hbm2e  
0            True                  False  
1            True                  False  
2            True                  False  
3            True                  False  
4            True                  False  

[5 rows x 30 columns]

## 5️⃣ Train-Test Split
Split the dataset into training and testing sets.

In [11]:
# Example: Split based on a numerical condition
train_data = df[df['unit_name_encoded'] >= 6]
test_data = df[df['unit_name_encoded'] < 6]

train_data = train_data.sample(frac=0.2, random_state=42)

# Separate features and target

X_train = train_data.drop(columns=['max_memory_util',	'avg_memory_util',	'max_gpu_util',	'avg_gpu_util',	'max_gpu_temp',	'avg_gpu_temp', 'epoch_time',	'fit_time'])
y_train = train_data[['epoch_time', 'fit_time', 'max_memory_util', 'max_gpu_util']]
X_test = test_data.drop(columns=['max_memory_util',	'avg_memory_util',	'max_gpu_util',	'avg_gpu_util',	'max_gpu_temp',	'avg_gpu_temp', 'epoch_time',	'fit_time'])  # Replace 'fit_time_in_TF' with your target column
y_test = test_data[['epoch_time', 'fit_time', 'max_memory_util', 'max_gpu_util']]

In [ ]:
train_data.shape

(1553, 27)

## 6️⃣ Model Building with XGBoost
Define, train, and predict using the XGBoost Regressor.

In [12]:
xgb_model = XGBRegressor(
    n_estimators=100,
    learning_rate=0.1,
    max_depth=6,
    random_state=42,
    verbosity=1
)

# Train the model
xgb_model.fit(X_train, y_train)

XGBRegressor(base_score=None, booster=None, callbacks=None,
             colsample_bylevel=None, colsample_bynode=None,
             colsample_bytree=None, device=None, early_stopping_rounds=None,
             enable_categorical=False, eval_metric=None, feature_types=None,
             gamma=None, grow_policy=None, importance_type=None,
             interaction_constraints=None, learning_rate=0.1, max_bin=None,
             max_cat_threshold=None, max_cat_to_onehot=None,
             max_delta_step=None, max_depth=6, max_leaves=None,
             min_child_weight=None, missing=nan, monotone_constraints=None,
             multi_strategy=None, n_estimators=100, n_jobs=None,
             num_parallel_tree=None, random_state=42, ...)

In [14]:
# Predict on the test set
y_pred = xgb_model.predict(X_test)

In [15]:
y_pred[:10]

array([[21.514431 , 20.075377 ,  5.7195935, 48.045883 ],
       [19.894218 , 19.883572 , 10.0262985, 69.34461  ],
       [20.112694 , 20.007633 , 11.493458 , 73.78841  ],
       [12.975633 , 18.08273  ,  7.1654763, 45.41951  ],
       [12.418544 , 18.560135 ,  8.162864 , 59.944546 ],
       [12.637019 , 18.684196 ,  8.962711 , 67.1194   ],
       [ 6.4134297, 20.612186 , 10.105451 , 60.0018   ],
       [ 5.8482485, 21.089592 , 10.060244 , 67.4093   ],
       [ 5.8482485, 20.968369 , 10.259554 , 74.447716 ],
       [ 4.295031 , 22.474957 , 10.036483 , 67.872734 ]], dtype=float32)

## 7️⃣ Evaluation Metrics
Calculate MAPE, MSPE, RMSPE, and standard regression metrics.

In [16]:
def manualCalculate(df1):
  df1['fit_time_res'] = (df1['batch_time'] / df1['batch']) * df1['samples'] * df1['epochs']
  return df1[['fit_time_res']]

y_manual = manualCalculate(X_test[['batch_time', 'batch', 'samples', 'epochs']])

<ipython-input-16-84545122e16d>:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df1['fit_time_res'] = (df1['batch_time'] / df1['batch']) * df1['samples'] * df1['epochs']


In [17]:


mape__per_column, mspe_per_column, rmspe_per_column = calculate_mspe_rmspe(y_test, y_pred)

mse_per_column = mean_squared_error(y_test, y_pred, multioutput='raw_values')  # MSE for each column
rmse_per_column = np.sqrt(mse_per_column)  # RMSE for each column

# Display results
for i, (mse, rmse, mape, mspe, rmspe) in enumerate(zip(mse_per_column, rmse_per_column, mape__per_column, mspe_per_column, rmspe_per_column)):
    print(f"Target Column {i + 1}:")
    print(f"  MSE: {mse:.4f}")
    print(f"  RMSE: {rmse:.4f}")
    print(f"  MAPE: {rmse:.4f}%")
    print(f"  MSPE: {mspe:.4f}%")
    print(f"  RMSPE: {rmspe:.4f}%")

# Save the model for future use
joblib.dump(xgb_model, 'xgb_model_model.pkl')

# Example of loading the model
# loaded_model = joblib.load('random_forest_model.pkl')

Target Column 1:
  MSE: 1245.5831
  RMSE: 35.2928
  MAPE: 35.2928%
  MSPE: 42.7299%
  RMSPE: 6.5368%
Target Column 2:
  MSE: 4263.1022
  RMSE: 65.2924
  MAPE: 65.2924%
  MSPE: 43.7782%
  RMSPE: 6.6165%
Target Column 3:
  MSE: 99.2517
  RMSE: 9.9625
  MAPE: 9.9625%
  MSPE: inf%
  RMSPE: inf%
Target Column 4:
  MSE: 456.3985
  RMSE: 21.3635
  MAPE: 21.3635%
  MSPE: inf%
  RMSPE: inf%


['xgb_model_model.pkl']

In [18]:


mape__per_column, mspe_per_column, rmspe_per_column = calculate_mspe_rmspe(y_test[['fit_time']], y_manual)

mse_per_column = mean_squared_error(y_test[['fit_time']], y_manual, multioutput='raw_values')  # MSE for each column
rmse_per_column = np.sqrt(mse_per_column)  # RMSE for each column

# Display results
for i, (mse, rmse, mape, mspe, rmspe) in enumerate(zip(mse_per_column, rmse_per_column, mape__per_column, mspe_per_column, rmspe_per_column)):
    print(f"Target Column {i + 1}:")
    print(f"  MSE: {mse:.4f}")
    print(f"  RMSE: {rmse:.4f}")
    print(f"  MAPE: {rmse:.4f}%")

# Save the model for future use
joblib.dump(xgb_model, 'xgb_model_model.pkl')

# Example of loading the model
# loaded_model = joblib.load('random_forest_model.pkl')

Target Column 1:
  MSE: 111.3580
  RMSE: 10.5526
  MAPE: 10.5526%


['xgb_model_model.pkl']

In [19]:
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score
import matplotlib.pyplot as plt
import seaborn as sns
import numpy as np

In [22]:
# Standard Regression Metrics
mae = mean_absolute_error(y_test, y_pred)
rmse = mean_squared_error(y_test, y_pred, squared=False)
r2 = r2_score(y_test, y_pred)

print(f'MAE: {mae:.4f}')
print(f'RMSE: {rmse:.4f}')
print(f'R²: {r2:.4f}')

MAE: 24.9825
RMSE: 32.9778
R²: 0.2661


/usr/local/lib/python3.11/dist-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(


## 9️⃣ Conclusion
Summarize key insights from the model performance and visualizations.

### ✅ In Conclusion:
- The XGBoost model provides a reasonable baseline for predicting CNN resource usage.
- Visualization highlights areas where predictions deviate.
- Feature importance gives insights into which factors most influence fit time.

For future work, hyperparameter tuning and advanced models could improve accuracy.